In [1]:
import os
from dotenv import load_dotenv
load_dotenv()
from langchain_groq import ChatGroq

groq_api_key = os.getenv("GROQ_API_KEY")

llm = ChatGroq(groq_api_key=groq_api_key, model_name='Llama3-8b-8192')

In [2]:
os.environ['HF_TOKEN'] = os.getenv("HF_TOKEN")
from langchain_huggingface import HuggingFaceEmbeddings
embeddings = HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")

/home/mahfuj/miniconda3/envs/langchain/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [3]:
from langchain_chroma import Chroma
from langchain_community.document_loaders import WebBaseLoader
from langchain_core.prompts import ChatPromptTemplate
from langchain_text_splitters import RecursiveCharacterTextSplitter

from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain

USER_AGENT environment variable not set, consider setting it to identify your requests.


In [4]:
import bs4
loader = WebBaseLoader(
    # web_path=("https://lilianweng.github.io/posts/2023-06-23-agent/",),
    web_path=("https://arxiv.org/pdf/2308.08465",),
    # bs_kwargs=dict(
    #     parse_only=bs4.SoupStrainer(
    #         class_=("post-content", "post-title", "post-header")
    #     )
    # ),
)

docs = loader.load()
docs

[Document(metadata={'source': 'https://arxiv.org/pdf/2308.08465'}, page_content='%PDF-1.5\n%�\n55 0 obj\n<< /Filter /FlateDecode /Length 2995 >>\nstream\nxڭY�s۸\x11\x7f��B��#\x00� �}IzI����M�������(��D*$�8��\x1f\x00ER���ދ\x05,���~�v\x01����Ƿ�^��fY��ۮ�N���Uf��q��۬�#u��Ҩ����Qy��\x0c�DE��\x1a\x07:*�\rS~��Өj��Ņ����?�U���\x1e*�=��Z��ƚ�o�b8wU\x0f�� ��p��M�U�p���m�a2�`���ٰ�x}S�@\x02�6U�K��aߞ\x07^>���x:�͎\x17YcX\x00\x01\r�ʶ)��Z�¨��¦�\x00\r,�\x07*�$\x16G�Do�o���#�\t\x07����\x06�\r��n\x1b&\x1e\n2!��:���}��\x1c�*M�á����<�uŦ��\x0e�L\u074c�%�dI��X�^\x02Ϋ��ɠ0���\x03\reT\x16��L\x07�P0\x0b��}���NH���>��q�\x1e@\x01\x1c\t@8�~�PpZ\x0e>t`��ou�w{bY\x7f�Mi\n�\x13<���Ap��d���%/@D��� �J�\x7fT\x07N\x11mRp��h�>���~&�������(+�VW�1t\x1c\u0379\\7<��À��}��S�z�����)�S��n��q$�\x00\x1f{\u07bf������\x07|G�\x056\x08Y�j��\u070f�b\r��b���(\x03���\x06�?ݤ\x19\x00[M��\x14���>�\x0c��.\x1a�\x1e+@-v@ϔ{� x�\x16\x13�ouq\x13ϝR\x06�����6����C�?�M�]\x12�hps\x05>�L����dut/�\x07&9�tn�sIf\x03���;@��X�t��c��:�:�0�[�>\x13��#�\tڰ\t��Լʪ��u

In [5]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
splits = text_splitter.split_documents(docs)
vector_store = Chroma.from_documents(documents=splits, embedding=embeddings)
retriever = vector_store.as_retriever()
retriever

VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_chroma.vectorstores.Chroma object at 0x75188c263970>, search_kwargs={})

In [6]:
## Prompt Template
system_prompt = (
    "You are an assistant for question-answering tasks."
    "Use the following pieces of retrieved context to answer "
    "the question. If you don't know the answer, say that you "
    "don't know. Use three sentences maximum and keep the "
    "answer concise."
    "\n\n"
    "{context}"
)

prompt = ChatPromptTemplate(
    [
        ("system", system_prompt),
        ("human", "{input}")
    ]
)

In [7]:
# question_answer_chain = create_stuff_documents_chain(llm, prompt)
# rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [8]:
# response = rag_chain.invoke({'input': "What is Self-Refelction"})
# response['answer']

In [9]:
# rag_chain.invoke({'input': "How do we achieve it?"})

# Add Chat History

In [10]:
from langchain.chains import create_history_aware_retriever
from langchain_core.prompts import MessagesPlaceholder

contextualize_q_system_prompt = (
    "Given a chat history and the latest user question "
    "which might reference context in the chat history "
    "formulate a stand alone question which can be understood "
    "without the chat history. Do not answer the question, "
    "just formulate it if needed and otherwise return it as is."
)

contextualize_q_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", contextualize_q_system_prompt),
        MessagesPlaceholder("chat_history"),
        ("human", "{input}"),
    ]
)

In [11]:
history_aware_retriever = create_history_aware_retriever(llm, retriever, contextualize_q_prompt)
history_aware_retriever

RunnableBinding(bound=RunnableBranch(branches=[(RunnableLambda(lambda x: not x.get('chat_history', False)), RunnableLambda(lambda x: x['input'])
| VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_chroma.vectorstores.Chroma object at 0x75188c263970>, search_kwargs={}))], default=ChatPromptTemplate(input_variables=['chat_history', 'input'], input_types={'chat_history': list[typing.Annotated[typing.Union[typing.Annotated[langchain_core.messages.ai.AIMessage, Tag(tag='ai')], typing.Annotated[langchain_core.messages.human.HumanMessage, Tag(tag='human')], typing.Annotated[langchain_core.messages.chat.ChatMessage, Tag(tag='chat')], typing.Annotated[langchain_core.messages.system.SystemMessage, Tag(tag='system')], typing.Annotated[langchain_core.messages.function.FunctionMessage, Tag(tag='function')], typing.Annotated[langchain_core.messages.tool.ToolMessage, Tag(tag='tool')], typing.Annotated[langchain_core.messages.ai.AIMessageChunk, Tag(tag='AIMessageChu

In [12]:
qa_prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        MessagesPlaceholder("chat_history"),
        ("human", "{input}"),
    ]
)

In [13]:
question_answer_chain = create_stuff_documents_chain(llm, qa_prompt)
rag_chain = create_retrieval_chain(history_aware_retriever, question_answer_chain)

In [14]:
from langchain_core.messages import AIMessage, HumanMessage
chat_history = []
question1 = "What is Self-Reflection"
response1 = rag_chain.invoke({"input": question1, "chat_history": chat_history})

chat_history.extend(
    [
        HumanMessage(content=question1),
        AIMessage(content=response1["answer"]),
    ]
)

question2 = "How do we achieve it?"
response2 = rag_chain.invoke({"input": question2, "chat_history": chat_history})
response2["answer"]

"I don't know the answer to that question based on the provided context."

In [15]:
chat_history

[HumanMessage(content='What is Self-Reflection', additional_kwargs={}, response_metadata={}),
 AIMessage(content="I don't know the answer to that question based on the provided context.", additional_kwargs={}, response_metadata={})]

# Session ID

In [16]:
from langchain_community.chat_message_histories import ChatMessageHistory
from langchain_core.chat_history import BaseChatMessageHistory
from langchain_core.runnables.history import RunnableWithMessageHistory

store = {}

def get_session_history(session_id: str) -> BaseChatMessageHistory:
    if session_id not in store:
        store[session_id] = ChatMessageHistory()
    return store[session_id]

conversation_rag_chain = RunnableWithMessageHistory(
    rag_chain,
    get_session_history,
    input_messages_key="input",
    history_messages_key="chat_history",
    output_messages_key="answer",
)

In [17]:
print(conversation_rag_chain.invoke(
    {"input": "What is the context about?"},
    config= {
        "configurable": {"session_id": "abc123"}
    },
)["answer"])

I don't know. The provided context appears to be a jumbled mix of random characters and does not seem to form a coherent message or topic.


In [18]:
# print(conversation_rag_chain.invoke(
#     {"input": ""},
#     config= {
#         "configurable": {"session_id": "abc123"}
#     },
# )["answer"])